In [1]:
import numpy as np
import pandas as pd
import seaborn.apionly as sns
import matplotlib.pyplot as plt
sns.set()
color = sns.color_palette()

In [2]:
#setup para el notebook

%matplotlib inline
pd.options.display.max_rows = 10
pd.options.display.float_format = '{:,.2f}'.format
plt.rcParams['figure.figsize'] = (16, 12)

In [3]:
import os
for data_dir in ["C:\\Users\Rafael\\Documents\\data\\instacart\\raw",
                 "C:/Users/rcrescenzi/Documents/Personal/data/instacart/raw"]:
    if os.path.exists(data_dir):
        print(data_dir)
        break
orders = pd.read_csv(data_dir + "/orders.csv", index_col="order_id")

C:\Users\Rafael\Documents\data\instacart\raw


In [4]:
valid_users = orders[orders.eval_set == "train"].user_id.sample(frac=0.1)
valid_users

order_id
1957420     81530
2852602     25950
1690117     96019
2929579    165219
2246337     98641
            ...  
1438171    129589
2783436    120341
309375      47297
640527      76252
2721521       378
Name: user_id, dtype: int64

In [5]:
orders = orders[orders.user_id.isin(valid_users)]
orders

user_id eval_set  order_number  order_dow  order_hour_of_day  \
order_id                                                                 
2565571         7    prior             1          3                  9   
2402008         7    prior             2          1                 19   
121053          7    prior             3          0                 18   
1695742         7    prior             4          2                 10   
3321109         7    prior             5          5                 18   
...           ...      ...           ...        ...                ...   
2177783    206198    prior             4          5                 11   
2874919    206198    prior             5          1                 11   
2841060    206198    prior             6          6                 16   
320997     206198    prior             7          6                 16   
2951304    206198    train             8          6                 12   

          days_since_prior_order  
order_id                          
2565571                      nan  
2402008                    30.00  
121053                     30.00  
1695742                     9.00  
3321109                     3.00  
...                          ...  
2177783                    26.00  
2874919                     3.00  
2841060                    30.00  
320997                      7.00  
2951304                    30.00  

[213852 rows x 6 columns]

In [6]:
def make_df(path):
    res = []
    for i, cand in enumerate(pd.read_csv(path, chunksize=100000)):
        temp =  cand.join(orders.user_id, on="order_id")
        temp = temp[temp.user_id.isin(valid_users)]
        res.append(temp.join(orders.drop("user_id", axis=1), on="order_id"))
        if (i % 100) == 0:
            print("haciendo", i+1)
            print(temp)
    return pd.concat(res)

In [7]:
train = make_df(data_dir + "/order_products__train.csv")
train

haciendo 1
       order_id  product_id  add_to_cart_order  reordered   user_id
32           98        8859                  1          1 56,463.00
33           98       19731                  2          1 56,463.00
34           98       43654                  3          1 56,463.00
35           98       13176                  4          1 56,463.00
36           98        4357                  5          1 56,463.00
...         ...         ...                ...        ...       ...
99884    246502       24964                 16          1 82,775.00
99885    246502        5212                 17          0 82,775.00
99886    246502       17395                 18          1 82,775.00
99887    246502       36994                 19          1 82,775.00
99888    246502        1364                 20          0 82,775.00

[10199 rows x 5 columns]


order_id  product_id  add_to_cart_order  reordered    user_id  \
32             98        8859                  1          1  56,463.00   
33             98       19731                  2          1  56,463.00   
34             98       43654                  3          1  56,463.00   
35             98       13176                  4          1  56,463.00   
36             98        4357                  5          1  56,463.00   
...           ...         ...                ...        ...        ...   
1384592   3421049       17706                  2          0 189,544.00   
1384593   3421049       33424                  3          1 189,544.00   
1384594   3421049       17299                  4          0 189,544.00   
1384595   3421049       26800                  5          0 189,544.00   
1384596   3421049       34243                  6          0 189,544.00   

        eval_set  order_number  order_dow  order_hour_of_day  \
32         train            41          3                  8   
33         train            41          3                  8   
34         train            41          3                  8   
35         train            41          3                  8   
36         train            41          3                  8   
...          ...           ...        ...                ...   
1384592    train             4          1                  9   
1384593    train             4          1                  9   
1384594    train             4          1                  9   
1384595    train             4          1                  9   
1384596    train             4          1                  9   

         days_since_prior_order  
32                        14.00  
33                        14.00  
34                        14.00  
35                        14.00  
36                        14.00  
...                         ...  
1384592                    3.00  
1384593                    3.00  
1384594                    3.00  
1384595                    3.00  
1384596                    3.00  

[139162 rows x 10 columns]

In [8]:
train.user_id.value_counts().sort_index()

7.00           9
29.00         17
47.00          6
49.00          6
63.00         14
              ..
206,132.00     8
206,144.00    14
206,153.00    26
206,178.00    14
206,198.00    13
Name: user_id, dtype: int64

In [9]:
prior = make_df(data_dir + "/order_products__prior.csv")
prior

haciendo 1
       order_id  product_id  add_to_cart_order  reordered    user_id
61            8       23423                  1          1   3,107.00
125          14       20392                  1          1  18,194.00
126          14       27845                  2          1  18,194.00
127          14         162                  3          1  18,194.00
128          14        2452                  4          1  18,194.00
...         ...         ...                ...        ...        ...
99812     10544       43739                  7          0 180,310.00
99813     10544        3399                  8          0 180,310.00
99814     10544       16797                  9          0 180,310.00
99815     10544       13032                 10          0 180,310.00
99816     10544       29363                 11          0 180,310.00

[6393 rows x 5 columns]
haciendo 101
          order_id  product_id  add_to_cart_order  reordered   user_id
10000213   1055870       26307                  1   

order_id  product_id  add_to_cart_order  reordered   user_id  \
61               8       23423                  1          1  3,107.00   
125             14       20392                  1          1 18,194.00   
126             14       27845                  2          1 18,194.00   
127             14         162                  3          1 18,194.00   
128             14        2452                  4          1 18,194.00   
...            ...         ...                ...        ...       ...   
32433840   3421008       13380                  1          1 51,596.00   
32433841   3421008       47209                  2          1 51,596.00   
32433842   3421008       46069                  3          1 51,596.00   
32433843   3421008       43961                  4          0 51,596.00   
32433916   3421017        2447                  1          1 30,372.00   

         eval_set  order_number  order_dow  order_hour_of_day  \
61          prior             5          4                  6   
125         prior            49          3                 15   
126         prior            49          3                 15   
127         prior            49          3                 15   
128         prior            49          3                 15   
...           ...           ...        ...                ...   
32433840    prior             6          5                 20   
32433841    prior             6          5                 20   
32433842    prior             6          5                 20   
32433843    prior             6          5                 20   
32433916    prior            18          4                  8   

          days_since_prior_order  
61                         17.00  
125                         3.00  
126                         3.00  
127                         3.00  
128                         3.00  
...                          ...  
32433840                    1.00  
32433841                    1.00  
32433842                    1.00  
32433843                    1.00  
32433916                    2.00  

[2019230 rows x 10 columns]

In [10]:
train.drop(["add_to_cart_order", "eval_set"], axis=1, inplace=True)
train

order_id  product_id  reordered    user_id  order_number  order_dow  \
32             98        8859          1  56,463.00            41          3   
33             98       19731          1  56,463.00            41          3   
34             98       43654          1  56,463.00            41          3   
35             98       13176          1  56,463.00            41          3   
36             98        4357          1  56,463.00            41          3   
...           ...         ...        ...        ...           ...        ...   
1384592   3421049       17706          0 189,544.00             4          1   
1384593   3421049       33424          1 189,544.00             4          1   
1384594   3421049       17299          0 189,544.00             4          1   
1384595   3421049       26800          0 189,544.00             4          1   
1384596   3421049       34243          0 189,544.00             4          1   

         order_hour_of_day  days_since_prior_order  
32                       8                   14.00  
33                       8                   14.00  
34                       8                   14.00  
35                       8                   14.00  
36                       8                   14.00  
...                    ...                     ...  
1384592                  9                    3.00  
1384593                  9                    3.00  
1384594                  9                    3.00  
1384595                  9                    3.00  
1384596                  9                    3.00  

[139162 rows x 8 columns]

In [11]:
prior.drop(["add_to_cart_order", "eval_set"], axis=1, inplace=True)
prior

order_id  product_id  reordered   user_id  order_number  order_dow  \
61               8       23423          1  3,107.00             5          4   
125             14       20392          1 18,194.00            49          3   
126             14       27845          1 18,194.00            49          3   
127             14         162          1 18,194.00            49          3   
128             14        2452          1 18,194.00            49          3   
...            ...         ...        ...       ...           ...        ...   
32433840   3421008       13380          1 51,596.00             6          5   
32433841   3421008       47209          1 51,596.00             6          5   
32433842   3421008       46069          1 51,596.00             6          5   
32433843   3421008       43961          0 51,596.00             6          5   
32433916   3421017        2447          1 30,372.00            18          4   

          order_hour_of_day  days_since_prior_order  
61                        6                   17.00  
125                      15                    3.00  
126                      15                    3.00  
127                      15                    3.00  
128                      15                    3.00  
...                     ...                     ...  
32433840                 20                    1.00  
32433841                 20                    1.00  
32433842                 20                    1.00  
32433843                 20                    1.00  
32433916                  8                    2.00  

[2019230 rows x 8 columns]

In [12]:
valid_order_data = orders[orders.eval_set == "train"]
valid_order_data = valid_order_data[valid_order_data.user_id.isin(valid_users)]
valid_order_data = valid_order_data.reset_index().set_index("user_id").drop(["eval_set"], axis=1)
valid_order_data

order_id  order_number  order_dow  order_hour_of_day  \
user_id                                                         
7          525192            21          2                 11   
29        3110252            19          4                 11   
47        2906490             6          4                 22   
49         519514             9          4                 12   
63        2989905            40          6                  8   
...           ...           ...        ...                ...   
206132     329474             6          1                 18   
206144    1782820             6          5                 18   
206153     642502            14          0                  8   
206178     813551            20          4                 12   
206198    2951304             8          6                 12   

         days_since_prior_order  
user_id                          
7                          6.00  
29                        13.00  
47                        16.00  
49                         2.00  
63                        13.00  
...                         ...  
206132                     5.00  
206144                    30.00  
206153                    21.00  
206178                    11.00  
206198                    30.00  

[13121 rows x 5 columns]

In [13]:
%%time
valid_set = prior.groupby("user_id").product_id.apply(lambda g: g.unique()).rename("product_id")
valid_set = valid_set.reset_index().groupby("user_id").product_id.apply(lambda x: pd.Series(x.iloc[0]))
valid_set.index.names = ["user_id", "tirar"]
valid_set = valid_set.reset_index().drop("tirar", axis=1).join(valid_order_data, on="user_id")

Wall time: 4.64 s


In [17]:
valid_set = valid_set.join(train.set_index(["order_id", "product_id"]).reordered, on=["order_id", "product_id"])
valid_set

user_id  product_id  order_id  order_number  order_dow  \
0            7.00       13198    525192            21          2   
1            7.00       42803    525192            21          2   
2            7.00        8277    525192            21          2   
3            7.00       37602    525192            21          2   
4            7.00       40852    525192            21          2   
...           ...         ...       ...           ...        ...   
840891 206,198.00        5782   2951304             8          6   
840892 206,198.00       25890   2951304             8          6   
840893 206,198.00        9327   2951304             8          6   
840894 206,198.00       23032   2951304             8          6   
840895 206,198.00        8203   2951304             8          6   

        order_hour_of_day  days_since_prior_order  reordered  
0                      11                    6.00       1.00  
1                      11                    6.00        nan  
2                      11                    6.00        nan  
3                      11                    6.00        nan  
4                      11                    6.00       1.00  
...                   ...                     ...        ...  
840891                 12                   30.00        nan  
840892                 12                   30.00        nan  
840893                 12                   30.00        nan  
840894                 12                   30.00        nan  
840895                 12                   30.00        nan  

[840896 rows x 8 columns]

In [21]:
valid_set.reordered.fillna(-1).value_counts()

-1.00    757378
1.00      83518
Name: reordered, dtype: int64

In [22]:
train.reordered.fillna(-1).value_counts()

1    83518
0    55644
Name: reordered, dtype: int64

In [23]:
prior.reordered.fillna(-1).value_counts()

1    1178334
0     840896
Name: reordered, dtype: int64

In [24]:
def get_real(g): 
    x = g[g.reordered==1]
    x = set(x.product_id.values)
    if len(x) == 0:
        x = set([0])
    return x

real = train.groupby("user_id").apply(get_real)

In [44]:
%%time
temp_prior = prior.groupby("user_id").apply(lambda x: x[x.order_number < x.order_number.max()])

Wall time: 16.9 s


In [45]:
temp_prior

order_id  product_id  reordered    user_id  order_number  \
user_id                                                                         
7.00       221645       23391       13198          1       7.00            17   
           221646       23391       42803          1       7.00            17   
           221647       23391        8277          1       7.00            17   
           221648       23391       37602          1       7.00            17   
           221649       23391       40852          1       7.00            17   
...                       ...         ...        ...        ...           ...   
206,198.00 27263872   2874919       48634          1 206,198.00             5   
           27263873   2874919       25890          0 206,198.00             5   
           27263874   2874919        9327          0 206,198.00             5   
           27263875   2874919       23032          0 206,198.00             5   
           27263876   2874919        8203          0 206,198.00             5   

                     order_dow  order_hour_of_day  days_since_prior_order  
user_id                                                                    
7.00       221645            0                 10                   28.00  
           221646            0                 10                   28.00  
           221647            0                 10                   28.00  
           221648            0                 10                   28.00  
           221649            0                 10                   28.00  
...                        ...                ...                     ...  
206,198.00 27263872          1                 11                    3.00  
           27263873          1                 11                    3.00  
           27263874          1                 11                    3.00  
           27263875          1                 11                    3.00  
           27263876          1                 11                    3.00  

[1882139 rows x 8 columns]

In [46]:
temp_prior = temp_prior.reset_index(drop=True)
temp_prior

order_id  product_id  reordered    user_id  order_number  order_dow  \
0           23391       13198          1       7.00            17          0   
1           23391       42803          1       7.00            17          0   
2           23391        8277          1       7.00            17          0   
3           23391       37602          1       7.00            17          0   
4           23391       40852          1       7.00            17          0   
...           ...         ...        ...        ...           ...        ...   
1882134   2874919       48634          1 206,198.00             5          1   
1882135   2874919       25890          0 206,198.00             5          1   
1882136   2874919        9327          0 206,198.00             5          1   
1882137   2874919       23032          0 206,198.00             5          1   
1882138   2874919        8203          0 206,198.00             5          1   

         order_hour_of_day  days_since_prior_order  
0                       10                   28.00  
1                       10                   28.00  
2                       10                   28.00  
3                       10                   28.00  
4                       10                   28.00  
...                    ...                     ...  
1882134                 11                    3.00  
1882135                 11                    3.00  
1882136                 11                    3.00  
1882137                 11                    3.00  
1882138                 11                    3.00  

[1882139 rows x 8 columns]

In [47]:
real_train = prior.groupby("user_id").apply(lambda x: x[x.order_number < x.order_number.max()]).groupby("user_id").apply(get_real)

In [49]:
real_train

user_id
7.00          {35333, 519, 45066, 13198, 10895, 21137, 40852...
29.00         {39170, 33027, 20874, 39185, 9875, 48800, 4829...
47.00                                     {15120, 24852, 24838}
49.00                                                       {0}
63.00         {5120, 2435, 24964, 7559, 46075, 12935, 31883,...
                                    ...                        
206,132.00              {45282, 48364, 21903, 6230, 29662, 671}
206,144.00                  {11461, 32141, 24852, 46650, 49279}
206,153.00    {40706, 28931, 41220, 24838, 649, 32650, 35601...
206,178.00    {17131, 26283, 12015, 44912, 23537, 46802, 461...
206,198.00                                {22312, 48634, 25861}
dtype: object

In [50]:
%%time
train_set = temp_prior.groupby("user_id").product_id.apply(lambda g: g.unique()).rename("product_id")
train_set = train_set.reset_index().groupby("user_id").product_id.apply(lambda x: pd.Series(x.iloc[0]))
train_set.index.names = ["user_id", "tirar"]
train_set = train_set.reset_index().drop("tirar", axis=1).join(valid_order_data, on="user_id")

Wall time: 4.17 s


In [52]:
train_set = train_set.join(train.set_index(["order_id", "product_id"]).reordered, on=["order_id", "product_id"])
train_set

user_id  product_id  order_id  order_number  order_dow  \
0            7.00       13198    525192            21          2   
1            7.00       42803    525192            21          2   
2            7.00        8277    525192            21          2   
3            7.00       37602    525192            21          2   
4            7.00       40852    525192            21          2   
...           ...         ...       ...           ...        ...   
783867 206,198.00        5782   2951304             8          6   
783868 206,198.00       25890   2951304             8          6   
783869 206,198.00        9327   2951304             8          6   
783870 206,198.00       23032   2951304             8          6   
783871 206,198.00        8203   2951304             8          6   

        order_hour_of_day  days_since_prior_order  reordered  
0                      11                    6.00       1.00  
1                      11                    6.00        nan  
2                      11                    6.00        nan  
3                      11                    6.00        nan  
4                      11                    6.00       1.00  
...                   ...                     ...        ...  
783867                 12                   30.00        nan  
783868                 12                   30.00        nan  
783869                 12                   30.00        nan  
783870                 12                   30.00        nan  
783871                 12                   30.00        nan  

[783872 rows x 8 columns]

In [53]:
valid_set.reordered.fillna(-1).value_counts()

-1.00    757378
1.00      83518
Name: reordered, dtype: int64

In [54]:
train_set.reordered.fillna(-1).value_counts()

-1.00    708177
1.00      75695
Name: reordered, dtype: int64

In [55]:
valid_set.reordered.fillna(0, inplace=True)
train_set.reordered.fillna(0, inplace=True)

In [56]:
from lightgbm import LGBMClassifier

depths = list(range(6, 20, 2))
ths = [i / 10 for i in range(1, 11)]

def get_true_pos(g):
    if not type(g["pred"]) == set:
        g["pred"] = set([0])
    x = g["real"].intersection(g["pred"])
    return x

def get_prec(true_pos, pred):
        if not type(pred) == set:
            pred = [0]
        return len(true_pos) / len(pred)

In [62]:
res = pd.DataFrame([], index=[str(d) for d in depths], columns=ths)

for depth in depths[0:1]:
    learner = LGBMClassifier(n_estimators=10000, max_depth=depth)
    learner.fit(prior.drop("reordered", axis=1), prior.reordered,
                early_stopping_rounds=10, eval_metric="binary_logloss",
                eval_set=[(train_set.drop("reordered", axis=1), train_set.reordered),
                          (valid_set.drop("reordered", axis=1), valid_set.reordered)])
    

[1]	valid_0's binary_logloss: 0.727206	valid_1's binary_logloss: 0.725902
Train until valid scores didn't improve in 10 rounds.
[2]	valid_0's binary_logloss: 0.759753	valid_1's binary_logloss: 0.757219
[3]	valid_0's binary_logloss: 0.790872	valid_1's binary_logloss: 0.787127
[4]	valid_0's binary_logloss: 0.820495	valid_1's binary_logloss: 0.815609
[5]	valid_0's binary_logloss: 0.848412	valid_1's binary_logloss: 0.842434
[6]	valid_0's binary_logloss: 0.874484	valid_1's binary_logloss: 0.867487
[7]	valid_0's binary_logloss: 0.89903	valid_1's binary_logloss: 0.891057
[8]	valid_0's binary_logloss: 0.922416	valid_1's binary_logloss: 0.913524
[9]	valid_0's binary_logloss: 0.944047	valid_1's binary_logloss: 0.934292
[10]	valid_0's binary_logloss: 0.964547	valid_1's binary_logloss: 0.95398
[11]	valid_0's binary_logloss: 0.983528	valid_1's binary_logloss: 0.972205
Early stopping, best iteration is:
[1]	valid_0's binary_logloss: 0.727206	valid_1's binary_logloss: 0.725902


In [68]:
res = pd.DataFrame([], index=[str(d) for d in depths], columns=ths)

for depth in depths:
    learner = LGBMClassifier(n_estimators=10000, max_depth=depth)
    learner.fit(train_set.drop("reordered", axis=1), train_set.reordered,
                early_stopping_rounds=10, eval_metric="auc",
                eval_set=[(train_set.drop("reordered", axis=1), train_set.reordered),
                          (valid_set.drop("reordered", axis=1), valid_set.reordered)])
    
    base_preds = valid_set[["user_id", "product_id"]].copy()
    base_preds["preds"] = learner.predict_proba(valid_set.drop("reordered", axis=1))[:, -1]
    for th in ths:
        preds = base_preds[base_preds.preds > th].groupby("user_id").product_id.apply(set)
        preds = pd.concat([real.rename("real"), preds.rename("pred")], axis=1)
        preds["true_pos"] = preds.apply(get_true_pos, axis=1)
        preds["prec"] = preds.apply(lambda g: get_prec(g.true_pos, g.pred), axis=1)
        preds["recall"] = preds.apply(lambda g: len(g.true_pos) / len(g["real"]), axis=1)
        preds["f1"] = 2 * (preds.prec * preds.recall) / (preds.prec + preds.recall)
        preds["f1"] = preds["f1"].fillna(0)
        res.loc[str(depth), th] = preds["f1"].mean()
    print(res)

[1]	valid_0's auc: 0.611884	valid_1's auc: 0.610346
Train until valid scores didn't improve in 10 rounds.
[2]	valid_0's auc: 0.6133	valid_1's auc: 0.611944
[3]	valid_0's auc: 0.61451	valid_1's auc: 0.612873
[4]	valid_0's auc: 0.615089	valid_1's auc: 0.613486
[5]	valid_0's auc: 0.6159	valid_1's auc: 0.614195
[6]	valid_0's auc: 0.616166	valid_1's auc: 0.614464
[7]	valid_0's auc: 0.616316	valid_1's auc: 0.614652
[8]	valid_0's auc: 0.616623	valid_1's auc: 0.614922
[9]	valid_0's auc: 0.616829	valid_1's auc: 0.615116
[10]	valid_0's auc: 0.617337	valid_1's auc: 0.615521
[11]	valid_0's auc: 0.617576	valid_1's auc: 0.615794
[12]	valid_0's auc: 0.617826	valid_1's auc: 0.61598
[13]	valid_0's auc: 0.618174	valid_1's auc: 0.616395
[14]	valid_0's auc: 0.618232	valid_1's auc: 0.61641
[15]	valid_0's auc: 0.618532	valid_1's auc: 0.616665
[16]	valid_0's auc: 0.618626	valid_1's auc: 0.616798
[17]	valid_0's auc: 0.619046	valid_1's auc: 0.617244
[18]	valid_0's auc: 0.619318	valid_1's auc: 0.617537
[19]	val

[155]	valid_0's auc: 0.668027	valid_1's auc: 0.663931
[156]	valid_0's auc: 0.668161	valid_1's auc: 0.664059
[157]	valid_0's auc: 0.668292	valid_1's auc: 0.664174
[158]	valid_0's auc: 0.668401	valid_1's auc: 0.664291
[159]	valid_0's auc: 0.668484	valid_1's auc: 0.664367
[160]	valid_0's auc: 0.668674	valid_1's auc: 0.664546
[161]	valid_0's auc: 0.668782	valid_1's auc: 0.664644
[162]	valid_0's auc: 0.669074	valid_1's auc: 0.664904
[163]	valid_0's auc: 0.66937	valid_1's auc: 0.665189
[164]	valid_0's auc: 0.66949	valid_1's auc: 0.665302
[165]	valid_0's auc: 0.669691	valid_1's auc: 0.665492
[166]	valid_0's auc: 0.669801	valid_1's auc: 0.665588
[167]	valid_0's auc: 0.66992	valid_1's auc: 0.665702
[168]	valid_0's auc: 0.670075	valid_1's auc: 0.665845
[169]	valid_0's auc: 0.670199	valid_1's auc: 0.665962
[170]	valid_0's auc: 0.670268	valid_1's auc: 0.666023
[171]	valid_0's auc: 0.670514	valid_1's auc: 0.666275
[172]	valid_0's auc: 0.670814	valid_1's auc: 0.666575
[173]	valid_0's auc: 0.670997	v

[308]	valid_0's auc: 0.692142	valid_1's auc: 0.686776
[309]	valid_0's auc: 0.692377	valid_1's auc: 0.686989
[310]	valid_0's auc: 0.692455	valid_1's auc: 0.687059
[311]	valid_0's auc: 0.692551	valid_1's auc: 0.687149
[312]	valid_0's auc: 0.692609	valid_1's auc: 0.687199
[313]	valid_0's auc: 0.692712	valid_1's auc: 0.687289
[314]	valid_0's auc: 0.692928	valid_1's auc: 0.687489
[315]	valid_0's auc: 0.692979	valid_1's auc: 0.687544
[316]	valid_0's auc: 0.693048	valid_1's auc: 0.687612
[317]	valid_0's auc: 0.693164	valid_1's auc: 0.687724
[318]	valid_0's auc: 0.693241	valid_1's auc: 0.687797
[319]	valid_0's auc: 0.693323	valid_1's auc: 0.687869
[320]	valid_0's auc: 0.693371	valid_1's auc: 0.687917
[321]	valid_0's auc: 0.69352	valid_1's auc: 0.688055
[322]	valid_0's auc: 0.693696	valid_1's auc: 0.688228
[323]	valid_0's auc: 0.693844	valid_1's auc: 0.68837
[324]	valid_0's auc: 0.694027	valid_1's auc: 0.688545
[325]	valid_0's auc: 0.694265	valid_1's auc: 0.688783
[326]	valid_0's auc: 0.694462	

[461]	valid_0's auc: 0.707406	valid_1's auc: 0.701021
[462]	valid_0's auc: 0.707464	valid_1's auc: 0.701077
[463]	valid_0's auc: 0.707597	valid_1's auc: 0.701181
[464]	valid_0's auc: 0.707702	valid_1's auc: 0.701277
[465]	valid_0's auc: 0.7078	valid_1's auc: 0.701378
[466]	valid_0's auc: 0.707888	valid_1's auc: 0.701458
[467]	valid_0's auc: 0.708057	valid_1's auc: 0.70162
[468]	valid_0's auc: 0.70815	valid_1's auc: 0.701706
[469]	valid_0's auc: 0.708244	valid_1's auc: 0.701799
[470]	valid_0's auc: 0.708292	valid_1's auc: 0.701843
[471]	valid_0's auc: 0.708468	valid_1's auc: 0.702006
[472]	valid_0's auc: 0.708559	valid_1's auc: 0.702093
[473]	valid_0's auc: 0.708646	valid_1's auc: 0.702177
[474]	valid_0's auc: 0.708735	valid_1's auc: 0.702256
[475]	valid_0's auc: 0.708762	valid_1's auc: 0.702278
[476]	valid_0's auc: 0.708829	valid_1's auc: 0.702341
[477]	valid_0's auc: 0.708903	valid_1's auc: 0.702406
[478]	valid_0's auc: 0.709017	valid_1's auc: 0.702521
[479]	valid_0's auc: 0.70914	val

[614]	valid_0's auc: 0.72036	valid_1's auc: 0.713228
[615]	valid_0's auc: 0.720391	valid_1's auc: 0.713256
[616]	valid_0's auc: 0.720455	valid_1's auc: 0.713316
[617]	valid_0's auc: 0.72051	valid_1's auc: 0.713368
[618]	valid_0's auc: 0.720572	valid_1's auc: 0.71342
[619]	valid_0's auc: 0.72063	valid_1's auc: 0.713474
[620]	valid_0's auc: 0.720732	valid_1's auc: 0.713566
[621]	valid_0's auc: 0.720815	valid_1's auc: 0.713641
[622]	valid_0's auc: 0.720888	valid_1's auc: 0.71371
[623]	valid_0's auc: 0.720941	valid_1's auc: 0.713758
[624]	valid_0's auc: 0.720985	valid_1's auc: 0.713794
[625]	valid_0's auc: 0.721092	valid_1's auc: 0.7139
[626]	valid_0's auc: 0.721157	valid_1's auc: 0.713961
[627]	valid_0's auc: 0.721245	valid_1's auc: 0.714045
[628]	valid_0's auc: 0.721338	valid_1's auc: 0.714121
[629]	valid_0's auc: 0.721384	valid_1's auc: 0.714164
[630]	valid_0's auc: 0.72144	valid_1's auc: 0.714215
[631]	valid_0's auc: 0.721511	valid_1's auc: 0.714281
[632]	valid_0's auc: 0.721544	valid_

...

[9396]	valid_0's auc: 0.920188	valid_1's auc: 0.897077
[9397]	valid_0's auc: 0.920189	valid_1's auc: 0.897078
[9398]	valid_0's auc: 0.920195	valid_1's auc: 0.897083
[9399]	valid_0's auc: 0.920205	valid_1's auc: 0.897092
[9400]	valid_0's auc: 0.920208	valid_1's auc: 0.897095
[9401]	valid_0's auc: 0.920218	valid_1's auc: 0.897105
[9402]	valid_0's auc: 0.920224	valid_1's auc: 0.897109
[9403]	valid_0's auc: 0.92023	valid_1's auc: 0.897115
[9404]	valid_0's auc: 0.920232	valid_1's auc: 0.897115
[9405]	valid_0's auc: 0.920242	valid_1's auc: 0.897124
[9406]	valid_0's auc: 0.920244	valid_1's auc: 0.897126
[9407]	valid_0's auc: 0.920247	valid_1's auc: 0.897128
[9408]	valid_0's auc: 0.920248	valid_1's auc: 0.89713
[9409]	valid_0's auc: 0.920256	valid_1's auc: 0.897137
[9410]	valid_0's auc: 0.920258	valid_1's auc: 0.89714
[9411]	valid_0's auc: 0.920264	valid_1's auc: 0.897145
[9412]	valid_0's auc: 0.920276	valid_1's auc: 0.897154
[9413]	valid_0's auc: 0.920281	valid_1's auc: 0.897161
[9414]	valid_

[9546]	valid_0's auc: 0.921131	valid_1's auc: 0.897899
[9547]	valid_0's auc: 0.921134	valid_1's auc: 0.8979
[9548]	valid_0's auc: 0.921139	valid_1's auc: 0.897903
[9549]	valid_0's auc: 0.921146	valid_1's auc: 0.897911
[9550]	valid_0's auc: 0.921154	valid_1's auc: 0.897919
[9551]	valid_0's auc: 0.921162	valid_1's auc: 0.897926
[9552]	valid_0's auc: 0.921163	valid_1's auc: 0.897926
[9553]	valid_0's auc: 0.921172	valid_1's auc: 0.897934
[9554]	valid_0's auc: 0.921175	valid_1's auc: 0.897935
[9555]	valid_0's auc: 0.921182	valid_1's auc: 0.897942
[9556]	valid_0's auc: 0.921188	valid_1's auc: 0.897948
[9557]	valid_0's auc: 0.921194	valid_1's auc: 0.897953
[9558]	valid_0's auc: 0.921198	valid_1's auc: 0.897956
[9559]	valid_0's auc: 0.921212	valid_1's auc: 0.897969
[9560]	valid_0's auc: 0.92122	valid_1's auc: 0.897976
[9561]	valid_0's auc: 0.921233	valid_1's auc: 0.897987
[9562]	valid_0's auc: 0.921244	valid_1's auc: 0.897997
[9563]	valid_0's auc: 0.921259	valid_1's auc: 0.898011
[9564]	valid_

[9696]	valid_0's auc: 0.922362	valid_1's auc: 0.89896
[9697]	valid_0's auc: 0.922366	valid_1's auc: 0.898962
[9698]	valid_0's auc: 0.922384	valid_1's auc: 0.898978
[9699]	valid_0's auc: 0.922402	valid_1's auc: 0.898997
[9700]	valid_0's auc: 0.922408	valid_1's auc: 0.899003
[9701]	valid_0's auc: 0.922417	valid_1's auc: 0.899009
[9702]	valid_0's auc: 0.92242	valid_1's auc: 0.899011
[9703]	valid_0's auc: 0.922422	valid_1's auc: 0.899014
[9704]	valid_0's auc: 0.922428	valid_1's auc: 0.89902
[9705]	valid_0's auc: 0.922439	valid_1's auc: 0.89903
[9706]	valid_0's auc: 0.922447	valid_1's auc: 0.899036
[9707]	valid_0's auc: 0.922461	valid_1's auc: 0.899048
[9708]	valid_0's auc: 0.922467	valid_1's auc: 0.899052
[9709]	valid_0's auc: 0.922473	valid_1's auc: 0.899057
[9710]	valid_0's auc: 0.922485	valid_1's auc: 0.899068
[9711]	valid_0's auc: 0.922493	valid_1's auc: 0.899075
[9712]	valid_0's auc: 0.922504	valid_1's auc: 0.899086
[9713]	valid_0's auc: 0.92251	valid_1's auc: 0.899091
[9714]	valid_0'

[9846]	valid_0's auc: 0.923726	valid_1's auc: 0.900184
[9847]	valid_0's auc: 0.923744	valid_1's auc: 0.900202
[9848]	valid_0's auc: 0.923751	valid_1's auc: 0.90021
[9849]	valid_0's auc: 0.923762	valid_1's auc: 0.90022
[9850]	valid_0's auc: 0.923764	valid_1's auc: 0.900221
[9851]	valid_0's auc: 0.923776	valid_1's auc: 0.900233
[9852]	valid_0's auc: 0.923789	valid_1's auc: 0.900245
[9853]	valid_0's auc: 0.923796	valid_1's auc: 0.900252
[9854]	valid_0's auc: 0.923807	valid_1's auc: 0.900262
[9855]	valid_0's auc: 0.923819	valid_1's auc: 0.900273
[9856]	valid_0's auc: 0.923823	valid_1's auc: 0.900277
[9857]	valid_0's auc: 0.923828	valid_1's auc: 0.900282
[9858]	valid_0's auc: 0.923835	valid_1's auc: 0.900289
[9859]	valid_0's auc: 0.923842	valid_1's auc: 0.900297
[9860]	valid_0's auc: 0.923851	valid_1's auc: 0.900305
[9861]	valid_0's auc: 0.923858	valid_1's auc: 0.900312
[9862]	valid_0's auc: 0.92386	valid_1's auc: 0.900313
[9863]	valid_0's auc: 0.923868	valid_1's auc: 0.900318
[9864]	valid_

[9996]	valid_0's auc: 0.924772	valid_1's auc: 0.901126
[9997]	valid_0's auc: 0.924786	valid_1's auc: 0.901139
[9998]	valid_0's auc: 0.924798	valid_1's auc: 0.901151
[9999]	valid_0's auc: 0.924805	valid_1's auc: 0.901157
[10000]	valid_0's auc: 0.924808	valid_1's auc: 0.90116
   0.10 0.20 0.30 0.40 0.50 0.60 0.70 0.80 0.90 1.00
6  0.37 0.41 0.32 0.22 0.16 0.11 0.09 0.07 0.06 0.06
8  0.40 0.47 0.36 0.26 0.18 0.13 0.09 0.07 0.06 0.06
10 0.41 0.48 0.38 0.27 0.19 0.13 0.09 0.07 0.06 0.06
12 0.41 0.49 0.39 0.28 0.19 0.13 0.09 0.07 0.06 0.06
14 0.42 0.50 0.39 0.28 0.19 0.13 0.09 0.07 0.06 0.06
16 0.41 0.50 0.39 0.28 0.19 0.13 0.09 0.07 0.06 0.06
18 0.41 0.50 0.39 0.27 0.19 0.13 0.09 0.07 0.06 0.06


In [69]:
res

0.10 0.20 0.30 0.40 0.50 0.60 0.70 0.80 0.90 1.00
6  0.37 0.41 0.32 0.22 0.16 0.11 0.09 0.07 0.06 0.06
8  0.40 0.47 0.36 0.26 0.18 0.13 0.09 0.07 0.06 0.06
10 0.41 0.48 0.38 0.27 0.19 0.13 0.09 0.07 0.06 0.06
12 0.41 0.49 0.39 0.28 0.19 0.13 0.09 0.07 0.06 0.06
14 0.42 0.50 0.39 0.28 0.19 0.13 0.09 0.07 0.06 0.06
16 0.41 0.50 0.39 0.28 0.19 0.13 0.09 0.07 0.06 0.06
18 0.41 0.50 0.39 0.27 0.19 0.13 0.09 0.07 0.06 0.06